In [1]:
import pandas as pd
import os
import numpy as np
from darwinutils.log import get_task_logger
from time import time
logger = get_task_logger(__name__)

In [2]:
train_data = pd.read_csv("picc/train.csv")
x_columns = train_data.columns.tolist()
x_columns.remove("标签")
train_x = train_data[x_columns].values
train_y = train_data["标签"].values
test_data = pd.read_csv("picc/validate.csv")
test_x = test_data[x_columns].values
test_y = test_data["标签"].values

In [3]:
def load_model(weight_file_path):
    global error_reason
    global return_code
    from modelmanager.model_service import load_sklearn_model
    from darwinutils.config import DARWIN_CONFIG
    import glob
    model_dump_files = glob.glob(os.path.join(weight_file_path, '*{}'.format(DARWIN_CONFIG.model_dump_suffix_ext)))
    model_dump_files += glob.glob(os.path.join(weight_file_path, '*model'))
    _ = list(map(lambda _: logger.debug("candicate model_dump_files for ml_model_train_post: {}".format(_)), enumerate(model_dump_files)))

    # load model
    model = None
    model_dump_file = None
    for model_dump_file in model_dump_files:
        if not model_dump_file.endswith(DARWIN_CONFIG.model_dump_suffix_ext):
            # TODO: this is for trace only and could be removed after all dump had been moved to standard dump file.
            logger.warning("Try loading model from non-standard dump file {}".format(model_dump_file))
        try:
            model = load_sklearn_model(model_dump_file, isTrain=False)
            if model is not None:
                break
        except:
            pass
    if model is None:
        logger.error("Load model for weight_file_path {} failed".format(weight_file_path))
        error_reason = "Load model for weight_file_path {} failed".format(weight_file_path)
        return_code = 500
    return model

In [4]:
model = load_model("picc/model")

Using TensorFlow backend.
/home/sysongyu/.conda/envs/darwin/lib/python3.6/site-packages/tensorflow/python/framework/dtypes.py:526: FutureWarning: Passing (type, 1) or '1type' as a synonym of type is deprecated; in a future version of numpy, it will be understood as (type, (1,)) / '(1,)type'.
  _np_qint8 = np.dtype([("qint8", np.int8, 1)])
/home/sysongyu/.conda/envs/darwin/lib/python3.6/site-packages/tensorflow/python/framework/dtypes.py:527: FutureWarning: Passing (type, 1) or '1type' as a synonym of type is deprecated; in a future version of numpy, it will be understood as (type, (1,)) / '(1,)type'.
  _np_quint8 = np.dtype([("quint8", np.uint8, 1)])
/home/sysongyu/.conda/envs/darwin/lib/python3.6/site-packages/tensorflow/python/framework/dtypes.py:528: FutureWarning: Passing (type, 1) or '1type' as a synonym of type is deprecated; in a future version of numpy, it will be understood as (type, (1,)) / '(1,)type'.
  _np_qint16 = np.dtype([("qint16", np.int16, 1)])
/home/sysongyu/.conda/e

In [5]:
def fake_predict_prob(X):
    rst, predict_y, predict_prob,  error_reason = model.predict_with_proba(x=X)
    if not rst:
        raise ValueError
    return np.array(predict_prob)

In [6]:
import shap
shap.initjs()

In [7]:
d2 = shap.kmeans(train_x, 10)
explainer = shap.KernelExplainer(fake_predict_prob, d2, link="identity")


In [8]:
output_shapes = []
for idx in range(len(test_x)):
    shap_values = explainer.shap_values(test_x[idx, :])
    output_shapes.append(shap_values[test_y[idx]])
    shap.force_plot(explainer.expected_value[test_y[idx]], shap_values[test_y[idx]], 
                features=[test_x[idx]], feature_names=x_columns,show=False,matplotlib=True).savefig('picc/outputs/test_data_{}.png'.format(idx+1))
shape_df = pd.DataFrame(output_shapes, columns=x_columns)
shape_df.to_csv("picc/outputs/shape_values.csv", index=False)

[2019-12-16 06:37:47] INFO [explain:346] num_full_subsets = 1
[2019-12-16 06:37:47] INFO [explain:357] remaining_weight_vector = [0.12275689 0.0826904  0.06267062 0.05066986 0.04267892 0.03697956
 0.03271269 0.02940103 0.02675824 0.0246021  0.02281115 0.02130128
 0.02001247 0.01890066 0.01793286 0.01708381 0.01633391 0.01566766
 0.01507268 0.01453897 0.01405835 0.01362405 0.01323046 0.01287288
 0.01254733 0.01225043 0.01197929 0.01173145 0.01150475 0.01129736
 0.01110767 0.01093427 0.01077594 0.01063162 0.01050037 0.01038136
 0.01027387 0.01017728 0.01009103 0.01001465 0.00994772 0.00988988
 0.00984084 0.00980034 0.00976819 0.0097442  0.00972828 0.00972034]
[2019-12-16 06:37:47] INFO [explain:358] num_paired_subset_sizes = 49
[2019-12-16 06:37:47] INFO [explain:397] weight_left = 0.8044997049879463
l1_reg="auto" is deprecated and in the next version (v0.29) the behavior will change from a conditional use of AIC to simply "num_features(10)"!
[2019-12-16 06:37:48] INFO [solve:560] np.sum

[2019-12-16 06:37:50] INFO [solve:605] phi = [ 0.03309709 -0.02021291 -0.09357691  0.          0.01142475  0.
 -0.00380852  0.03134403  0.00701659 -0.01829776  0.00418935  0.
  0.          0.         -0.00635046  0.00860043  0.00899175 -0.01737715
  0.00732398  0.         -0.00940014  0.          0.01224922  0.
  0.          0.          0.          0.01238439 -0.0253216  -0.00347482
 -0.01433886  0.02025191  0.         -0.00611268 -0.00273482  0.
 -0.02919703 -0.02116074  0.          0.0146582   0.          0.
  0.          0.          0.          0.01064376  0.          0.02070941
  0.00678891  0.00379788 -0.06981494  0.2567694   0.          0.06650139
 -0.01647671  0.          0.          0.01241189  0.05276694  0.01071446
  0.         -0.02045214  0.          0.          0.          0.
 -0.0051842   0.02512347  0.          0.          0.          0.
  0.          0.02233578  0.01991019  0.          0.          0.
  0.          0.          0.          0.          0.          0.
  0. 

l1_reg="auto" is deprecated and in the next version (v0.29) the behavior will change from a conditional use of AIC to simply "num_features(10)"!
[2019-12-16 06:37:53] INFO [solve:560] np.sum(w_aug) = 100.0
[2019-12-16 06:37:53] INFO [solve:561] np.sum(self.kernelWeights) = 1.0
[2019-12-16 06:37:53] INFO [solve:605] phi = [-0.05569478 -0.01572634 -0.01464651  0.          0.          0.
  0.0178792   0.02934834  0.          0.00696972  0.0136614  -0.01454204
  0.          0.          0.02305383  0.          0.          0.
 -0.003714    0.          0.          0.          0.          0.
  0.          0.          0.         -0.01506956  0.01426934 -0.04977013
  0.01065171  0.          0.01194475  0.          0.          0.
  0.          0.          0.          0.          0.          0.
  0.          0.         -0.01493092  0.03469622 -0.00402436 -0.05611951
  0.01182549 -0.02137793  0.43789213  0.0672609  -0.19455881  0.01086952
 -0.01434759  0.         -0.01664196  0.         -0.01189499

[2019-12-16 06:37:57] INFO [explain:346] num_full_subsets = 1
[2019-12-16 06:37:57] INFO [explain:357] remaining_weight_vector = [0.12525914 0.08446593 0.06408607 0.05187202 0.04374129 0.03794425
 0.03360611 0.03024089 0.02755701 0.02536894 0.023553   0.02202358
 0.02071956 0.0195961  0.0186196  0.01776439 0.0170105  0.01634219
 0.01574686 0.01521436 0.01473637 0.01430604 0.01391768 0.01356653
 0.01324856 0.01296038 0.01269908 0.01246219 0.01224756 0.01205337
 0.01187802 0.01172015 0.01157858 0.01145226 0.01134033 0.01124202
 0.01115668 0.01108376 0.0110228  0.01097342 0.01093532 0.01090827
 0.0108921  0.01088672]
[2019-12-16 06:37:57] INFO [explain:358] num_paired_subset_sizes = 44
[2019-12-16 06:37:57] INFO [explain:397] weight_left = 0.8006025766934114
l1_reg="auto" is deprecated and in the next version (v0.29) the behavior will change from a conditional use of AIC to simply "num_features(10)"!
[2019-12-16 06:37:57] INFO [solve:560] np.sum(w_aug) = 90.0
[2019-12-16 06:37:57] INFO [s

l1_reg="auto" is deprecated and in the next version (v0.29) the behavior will change from a conditional use of AIC to simply "num_features(10)"!
[2019-12-16 06:38:00] INFO [solve:560] np.sum(w_aug) = 86.0
[2019-12-16 06:38:00] INFO [solve:561] np.sum(self.kernelWeights) = 1.0
[2019-12-16 06:38:00] INFO [solve:605] phi = [ 0.01294323 -0.01884675  0.          0.         -0.02392109 -0.01181887
 -0.02101745  0.          0.          0.01787327  0.01383739  0.
  0.          0.          0.          0.01133329  0.          0.
  0.          0.          0.          0.          0.          0.
  0.          0.          0.          0.00912745 -0.01211194  0.
 -0.01230529  0.          0.00992766  0.          0.          0.00842099
  0.          0.          0.          0.          0.          0.
  0.          0.          0.          0.01496023  0.          0.
  0.         -0.01303565 -0.01633009  0.36247758  0.10613127  0.01263701
  0.          0.          0.          0.00826659  0.          0.01089

...

l1_reg="auto" is deprecated and in the next version (v0.29) the behavior will change from a conditional use of AIC to simply "num_features(10)"!
[2019-12-16 07:07:45] INFO [solve:560] np.sum(w_aug) = 86.0
[2019-12-16 07:07:45] INFO [solve:561] np.sum(self.kernelWeights) = 1.0
[2019-12-16 07:07:45] INFO [solve:605] phi = [ 0.          0.          0.         -0.02470035 -0.04036002 -0.01391522
 -0.03632243 -0.00705868  0.          0.         -0.0209758   0.
  0.          0.          0.          0.          0.01331768 -0.00907567
  0.0091153   0.          0.          0.          0.          0.
  0.          0.         -0.03251353  0.         -0.02249681  0.
  0.          0.         -0.01245727  0.          0.          0.
  0.          0.          0.          0.          0.          0.
  0.         -0.02367702  0.04558602  0.          0.          0.03402593
 -0.01844798  0.538018    0.01517436 -0.19018983  0.01927315  0.
  0.          0.          0.          0.          0.          0.
 -0.

More than 20 figures have been opened. Figures created through the pyplot interface (`matplotlib.pyplot.figure`) are retained until explicitly closed and may consume too much memory. (To control this warning, see the rcParam `figure.max_open_warning`).
[2019-12-16 07:07:48] INFO [explain:346] num_full_subsets = 1
[2019-12-16 07:07:48] INFO [explain:357] remaining_weight_vector = [0.12525914 0.08446593 0.06408607 0.05187202 0.04374129 0.03794425
 0.03360611 0.03024089 0.02755701 0.02536894 0.023553   0.02202358
 0.02071956 0.0195961  0.0186196  0.01776439 0.0170105  0.01634219
 0.01574686 0.01521436 0.01473637 0.01430604 0.01391768 0.01356653
 0.01324856 0.01296038 0.01269908 0.01246219 0.01224756 0.01205337
 0.01187802 0.01172015 0.01157858 0.01145226 0.01134033 0.01124202
 0.01115668 0.01108376 0.0110228  0.01097342 0.01093532 0.01090827
 0.0108921  0.01088672]
[2019-12-16 07:07:48] INFO [explain:358] num_paired_subset_sizes = 44
[2019-12-16 07:07:48] INFO [explain:397] weight_left = 

[2019-12-16 07:07:51] INFO [explain:358] num_paired_subset_sizes = 49
[2019-12-16 07:07:51] INFO [explain:397] weight_left = 0.8044997049879463
l1_reg="auto" is deprecated and in the next version (v0.29) the behavior will change from a conditional use of AIC to simply "num_features(10)"!
[2019-12-16 07:07:51] INFO [solve:560] np.sum(w_aug) = 99.0
[2019-12-16 07:07:51] INFO [solve:561] np.sum(self.kernelWeights) = 1.0
[2019-12-16 07:07:52] INFO [solve:605] phi = [ 0.         -0.03222636 -0.02020401 -0.012457    0.          0.
  0.04020267  0.          0.         -0.01147243  0.01663296 -0.0264221
  0.          0.          0.          0.          0.          0.
  0.         -0.01728598  0.          0.          0.          0.
  0.00824787  0.          0.00633024  0.03313261  0.01252032  0.
  0.00761521  0.02745748  0.          0.00783486  0.          0.
  0.          0.          0.          0.          0.          0.
  0.          0.          0.00933466 -0.01533674  0.          0.
  0.034

l1_reg="auto" is deprecated and in the next version (v0.29) the behavior will change from a conditional use of AIC to simply "num_features(10)"!
[2019-12-16 07:07:55] INFO [solve:560] np.sum(w_aug) = 98.0
[2019-12-16 07:07:55] INFO [solve:561] np.sum(self.kernelWeights) = 0.9999999999999997
[2019-12-16 07:07:55] INFO [solve:605] phi = [ 0.          0.0164564  -0.00984585 -0.01013491 -0.01891962  0.
 -0.03598392  0.05466049 -0.00646643  0.         -0.0195556   0.0271921
  0.          0.          0.         -0.00900692 -0.00222463  0.02196498
  0.          0.02233248  0.02765627  0.         -0.01333553  0.
 -0.01184073  0.          0.         -0.04935797 -0.03226131 -0.01009557
 -0.01253618 -0.03034011  0.         -0.04160772  0.0061122   0.
  0.01105942  0.          0.          0.          0.          0.
  0.          0.          0.         -0.03692809  0.02986049 -0.00816314
  0.0143714  -0.01172647  0.00546316 -0.20782177  0.02404987  0.00533327
  0.01700386  0.00761903  0.         -0

More than 20 figures have been opened. Figures created through the pyplot interface (`matplotlib.pyplot.figure`) are retained until explicitly closed and may consume too much memory. (To control this warning, see the rcParam `figure.max_open_warning`).


In [33]:
global_idx=5
shap_values = explainer.shap_values(test_x[global_idx, :])
shap.force_plot(explainer.expected_value[test_y[global_idx]], shap_values[test_y[global_idx]], 
            features=[test_x[global_idx]], feature_names=x_columns)

[2019-12-16 06:14:55] INFO [explain:346] num_full_subsets = 1
[2019-12-16 06:14:55] INFO [explain:357] remaining_weight_vector = [0.12314468 0.08297921 0.06291087 0.05088176 0.04287259 0.03716083
 0.03288523 0.0295673  0.02692    0.02476064 0.02296746 0.02145616
 0.02016655 0.01905448 0.01808687 0.01723842 0.01648946 0.01582447
 0.01523105 0.01469917 0.01422064 0.01378868 0.01339768 0.01304293
 0.01272044 0.01242684 0.01215924 0.01191518 0.01169252 0.01148943
 0.0113043  0.01113574 0.01098254 0.01084365 0.01071815 0.01060522
 0.01050417 0.01041439 0.01033536 0.01026661 0.01020776 0.01015849
 0.01011853 0.01008767 0.01006574 0.01005263 0.01004826]
[2019-12-16 06:14:55] INFO [explain:358] num_paired_subset_sizes = 47
[2019-12-16 06:14:55] INFO [explain:397] weight_left = 0.8032597061842652
l1_reg="auto" is deprecated and in the next version (v0.29) the behavior will change from a conditional use of AIC to simply "num_features(10)"!
[2019-12-16 06:14:56] INFO [solve:560] np.sum(w_aug) = 9

In [42]:
test_data[["134", "136", "135", "131", "122", "8", "97", "132", "18", "64", "121"]][:6]

134       136  135  131  122   8  97  132   18  64  121
0   25  1628.042   10   20   26  46  11   11  171   3  198
1   25     0.000   11   11   25   2  10    0  131   3  192
2   17   786.418   10   13   40   2   9    5   90   2  128
3   20  1011.136    8   27   45   3   4    1   66   2  103
4   25     0.000    1    1   28   1   2    0  114   4   92
5   25     0.000    7   13   44   1   6    0  265   1  393